# k-scheduling tests

In [1]:
import matplotlib.pyplot as plt
import numpy as np

from random import sample, seed
from tqdm import tqdm

from qiskit import QuantumCircuit, QuantumRegister, ClassicalRegister, Aer, transpile, assemble
from qiskit.algorithms import amplitude_estimators, EstimationProblem
from qiskit.algorithms import IterativeAmplitudeEstimation as BaseIterativeAmplitudeEstimation

from algorithms import IterativeAmplitudeEstimation, MaximumLikelihoodAmplitudeEstimation, FasterAmplitudeEstimation
from operators import *

In [2]:
# Define the estimation problem and oracle function
def good_state(state):
    bin_marked = [(n-len(bin(s))+2)*'0'+bin(s)[2:] for s in marked]
    return (state in bin_marked)

In [3]:
# use local simulator
aer_sim = Aer.get_backend('aer_simulator')
shots = 100

## IQAE: attempt exponential decay in the number of shots per iteration to account for deeper circuits.

In [4]:
# parameters for IQAE
alpha = 0.05
confint_method = 'chernoff'

In [ ]:
powers = range(2,7)
epsilons = [(1.0 / (10**power)) for power in powers]
num_experiments = 10

iae_results = [[0 for _ in range(len(epsilons))] for _ in range(num_experiments)]

for i in tqdm(range(num_experiments)):
    
    # random select
    n = 4
    N = 2**n
    k = np.random.randint(0, N+1)
    marked = sample(range(N), k)
    
    problem = EstimationProblem(
        state_preparation=A(n),  # A operator
        grover_operator=Q(n, marked),  # Q operator
        objective_qubits=range(n),
        is_good_state=good_state  # the "good" state Psi1 is identified as measuring |1> in qubit 0
    )
    
    print(k/N)
    
    for j, epsilon in enumerate(epsilons):
        
        IAE = IterativeAmplitudeEstimation(epsilon_target=epsilon, 
                                           alpha=alpha, 
                                           confint_method=confint_method, 
                                           quantum_instance=aer_sim,
                                           verbose=True)
        iae_results[i][j] = IAE.estimate(problem)

  0%|          | 0/10 [00:00<?, ?it/s]

0.5625
T: 7

Iteration 1
  k_i: 0
Iteration 2
  k_i: 1
Iteration 3
  k_i: 3
Iteration 4
  k_i: 9
Iteration 5
  k_i: 27
T: 10

Iteration 1
  k_i: 0
Iteration 2
  k_i: 1
Iteration 3
  k_i: 3
Iteration 4
  k_i: 3
  Ki-1 = Ki, shots summed
Iteration 5
  k_i: 3
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
Iteration 6
  k_i: 3
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
Iteration 7
  k_i: 3
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
Iteration 8
  k_i: 3
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
Iteration 9
  k_i: 3
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
Iteration 10
  k_i: 3
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, shots summed
  Ki-1 = Ki, 

In [ ]:
IAE_RESULT = iae_results

In [ ]:
iae_epsilon = np.array([[(res.confidence_interval_processed[1] - res.confidence_interval_processed[0]) / 2 for res in result_row] for result_row in IAE_RESULT])
iae_delta_c = np.array([[int(res.confidence_interval_processed[0] < k/N < res.confidence_interval_processed[1]) for res in result_row] for result_row in IAE_RESULT])
iae_nshots  = np.array([[res.num_oracle_queries for res in result_row] for result_row in IAE_RESULT])

In [ ]:
iae_epsilon = iae_epsilon.mean(axis=0)
iae_delta = 1 - iae_delta_c.mean(axis=0)
iae_nshots = iae_nshots.mean(axis=0)

In [ ]:
iae_delta_c

In [ ]:
plt.scatter(iae_epsilon, iae_delta)
plt.plot(iae_epsilon, iae_delta)

plt.xscale('log')
plt.ylim(-0.1,1.1)
plt.show()

In [ ]:
fig = plt.figure()
ax = plt.gca()
ax.scatter(iae_nshots, iae_epsilon)
ax.plot(iae_nshots, iae_epsilon)

ax.legend(['Base IAE'])
ax.set_yscale('log')
ax.set_xscale('log')
plt.xlim(1, 10**10)
plt.show()